## Turn your S&P500 portfolio into synthetic in-the-money calls.

#### This notebook researches a strategy in which:
1. You buy the S&P 500 (using an ETF);
2. You choose the value ```put_perc_otm```, which is the **percent below the S&P purchase price** to use as the strike price of a put that limits your downside exposure;
3. You choose the value ```years_to_hedge```, which is the duration of the put;
4. Actions to take as the S&P price moves and time passes:
  * S&P rises to  ``` 2 * put_perc_otm``` above current hedge strike: 
    * you sell the previous put, and purhase another put at a **higher** strike, and for the full ```years_to_hedge```, effectively buying diagonal put spreads
  * S&P falls to ```2 * put_perc_otm``` below the current hedge strike: 
    * you sell the previous put, and purhase another put at a **lower** strike, and for the full ```years_to_hedge```, effectively selling diagonal put spreads

#### The main benefit of this strategy
* The strategy is designed to provide continual insurance  of your long S&P position, using a rolling series of puts.  These puts effectively turn your S&P position into a call that still collects dividends.
* Depending on where the price of the S&P 500 is relative to the current put strike, you will either have a position that is long an in-the-money call (as the S&P 500 rises to newer all time highs, or an out of the money all (as the S&P falls from those all time highs).


## IF YOU WANT TO SEE WARNINGS, COMMENT THIS OUT

In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
import zipfile
import glob
import pandas as pd
import numpy as np

from argparse import ArgumentParser
from argparse import RawDescriptionHelpFormatter
import sys
import os
if  not './' in sys.path:
    sys.path.append('./')
if  not '../' in sys.path:
    sys.path.append('../')

from IPython.core.display import  HTML
from barchartacs import build_db
from barchartacs import db_info
import plotly.graph_objs as go
from plotly.offline import  init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.tools as tls
from plotly.graph_objs.layout import Font,Margin,Modebar
from IPython import display

import datetime
from dateutil.relativedelta import relativedelta
import io
from tqdm import tqdm,tqdm_notebook
from barchartacs import pg_pandas as pg
import mibian
import py_vollib
import importlib
from py_vollib import black
from py_vollib.black import implied_volatility
import ipdb,pdb
import traceback
import pandas_datareader.data as pdr
from scipy.stats import norm

from ipysheet import from_dataframe,to_dataframe
from dashapp import dashapp2 as dashapp
# import dash
import dash_html_components as html
import dash_core_components as dcc
import plotly.express as px



### important global variables

#### Step 01: define important parameters that are used in successive steps below

In [3]:
# define how far out of the money you want your hedge
# put_perc_otm = 0.125
put_perc_otm = 0.14
years_to_hedge = 2
# set the target percentage of stock
rebal_target = .6
# set the percentage of stock in the portfolio that forces a rebalance
rebal_adjust = .7


Define and display important dates and values

In [4]:
sp_data_end_date = datetime.datetime.now()
sp_data_beg_date = sp_data_end_date - relativedelta(years=30)
beg_date_str = datetime.datetime.strftime(sp_data_beg_date,'%Y-%m-%d')
end_date_str = datetime.datetime.strftime(sp_data_end_date,'%Y-%m-%d')
print(f"using put hedge {put_perc_otm * 100} percent out of the money")
print(f"put hedge duration = {years_to_hedge} years (this can be a fraction like 1.5)")
print(f"S&P history starts on {beg_date_str} and ends on {end_date_str}")


using put hedge 14.000000000000002 percent out of the money
put hedge duration = 2 years (this can be a fraction like 1.5)
S&P history starts on 1990-05-25 and ends on 2020-05-25


#### Step 02: define important functions that are used below

In [49]:
def dt_to_yyyymmdd(d):
    return int(d.year)*100*100 + int(d.month)*100 + int(d.day)

def str_to_yyyymmdd(d,sep='-'):
    try:
        dt = datetime.datetime.strptime(str(d)[:10],f'%Y{sep}%m{sep}%d')
    except:
        return None
    s = '%04d%02d%02d' %(dt.year,dt.month,dt.day)
    return int(s)

def str_to_date(d,sep='-'):
    try:
        dt = datetime.datetime.strptime(str(d)[:10],f'%Y{sep}%m{sep}%d')
    except:
        return None
    return dt


def fetch_history(symbol,dt_beg,dt_end):
    df = pdr.DataReader(symbol, 'yahoo', dt_beg, dt_end)
    # move index to date column, sort and recreate index
    df['date'] = df.index
    df = df.sort_values('date')
    df.index = list(range(len(df)))
    # make adj close the close
    df = df.drop(['Adj Close'],axis=1)
    cols = df.columns.values 
    cols_dict = {c:c[0].lower() + c[1:] for c in cols}
    df = df.rename(columns = cols_dict)
    df['settle_date'] = df.date.apply(str_to_yyyymmdd)
    return df


In [6]:
def plotly_plot(df_in,x_column,plot_title=None,
                y_left_label=None,y_right_label=None,
                bar_plot=False,width=800,height=400,
                number_of_ticks_display=20,
                yaxis2_cols=None,
                x_value_labels=None,
                modebar_orientation='v',modebar_color='grey',
                legend_x=None,legend_y=None):
    ya2c = [] if yaxis2_cols is None else yaxis2_cols
    ycols = [c for c in df_in.columns.values if c != x_column]
    # create tdvals, which will have x axis labels
    td = list(df_in[x_column]) 
    nt = len(df_in)-1 if number_of_ticks_display > len(df_in) else number_of_ticks_display
    spacing = len(td)//nt
    tdvals = td[::spacing]
    tdtext = tdvals
    if x_value_labels is not None:
        tdtext = [x_value_labels[i] for i in tdvals]
    
    # create data for graph
    data = []
    # iterate through all ycols to append to data that gets passed to go.Figure
    for ycol in ycols:
        if bar_plot:
            b = go.Bar(x=td,y=df_in[ycol],name=ycol,yaxis='y' if ycol not in ya2c else 'y2')
        else:
            b = go.Scatter(x=td,y=df_in[ycol],name=ycol,yaxis='y' if ycol not in ya2c else 'y2')
        data.append(b)

    # create a layout

    layout = go.Layout(
        title=plot_title,
        xaxis=dict(
            ticktext=tdtext,
            tickvals=tdvals,
            tickangle=45,
            type='category'),
        yaxis=dict(
            title='y main' if y_left_label is None else y_left_label
        ),
        yaxis2=dict(
            title='y alt' if y_right_label is None else y_right_label,
            overlaying='y',
            side='right'),
        autosize=True,
#         autosize=False,
#         width=width,
#         height=height,
        margin=Margin(
            b=100
        ),
        modebar={'orientation': modebar_orientation,'bgcolor':modebar_color}
    )

    fig = go.Figure(data=data,layout=layout)
    fig.update_layout(
        title={
            'text': plot_title,
            'y':0.9,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top'})
    if (legend_x is not None) and (legend_y is not None):
        fig.update_layout(legend=dict(x=legend_x, y=legend_y))
    return fig

def plotly_shaded_rectangles(beg_end_date_tuple_list,fig):
    ld_shapes = []
    for beg_end_date_tuple in beg_end_date_tuple_list:
        ld_beg = beg_end_date_tuple[0]
        ld_end = beg_end_date_tuple[1]
        ld_shape = dict(
            type="rect",
            # x-reference is assigned to the x-values
            xref="x",
            # y-reference is assigned to the plot paper [0,1]
            yref="paper",
#             x0=ld_beg[i],
            x0=ld_beg,
            y0=0,
#             x1=ld_end[i],
            x1=ld_end,
            y1=1,
            fillcolor="LightSalmon",
            opacity=0.5,
            layer="below",
            line_width=0,
        )
        ld_shapes.append(ld_shape)

    fig.update_layout(shapes=ld_shapes)
    return fig

## Create a hedge strategy and use data on ^GSPC from yahoo 

#### Step 03: get data

In [7]:
# fred_url = 'https://fred.stlouisfed.org/graph/fredgraph.csv?bgcolor=%23e1e9f0&chart_type=line&drp=0&fo=open%20sans&graph_bgcolor=%23ffffff&height=450&mode=fred&recession_bars=on&txtcolor=%23444444&ts=12&tts=12&width=1168&nt=0&thu=0&trc=0&show_legend=yes&show_axis_titles=yes&show_tooltip=yes&id=DGS1&scale=left&cosd=1962-01-02&coed=2021-05-01&line_color=%234572a7&link_values=false&line_style=solid&mark_type=none&mw=3&lw=2&ost=-99999&oet=99999&mma=0&fml=a&fq=Daily&fam=avg&fgst=lin&fgsnd=2009-06-01&line_index=1&transformation=lin&vintage_date=2021-05-04&revision_date=2021-05-04&nd=1962-01-02'
# df_1yr_rate = pd.read_csv(fred_url)

# df_1yr_rate.tail()

In [8]:
# dt_end = datetime.datetime.now()
# dt_beg = dt_end - datetime.timedelta(365*30)
df_spy = fetch_history('^GSPC', sp_data_beg_date, sp_data_end_date)
df_vix = fetch_history('^VIX',sp_data_beg_date,sp_data_end_date)
df_tnx = fetch_history('^TNX',sp_data_beg_date,sp_data_end_date)
fred_url = 'https://fred.stlouisfed.org/graph/fredgraph.csv?bgcolor=%23e1e9f0&chart_type=line&drp=0&fo=open%20sans&graph_bgcolor=%23ffffff&height=450&mode=fred&recession_bars=on&txtcolor=%23444444&ts=12&tts=12&width=1168&nt=0&thu=0&trc=0&show_legend=yes&show_axis_titles=yes&show_tooltip=yes&id=DGS1&scale=left&cosd=1962-01-02&coed=2021-05-01&line_color=%234572a7&link_values=false&line_style=solid&mark_type=none&mw=3&lw=2&ost=-99999&oet=99999&mma=0&fml=a&fq=Daily&fam=avg&fgst=lin&fgsnd=2009-06-01&line_index=1&transformation=lin&vintage_date=2021-05-04&revision_date=2021-05-04&nd=1962-01-02'
df_1yr_rate = pd.read_csv(fred_url)
dates_1yr = [datetime.datetime.strptime(d,'%Y-%m-%d') for d in df_1yr_rate.DATE.values]
df_1yr_rate['settle_date'] = [int(d.year)*100*100+int(d.month)*100+int(d.day) for d in dates_1yr]
df_1yr_rate = df_1yr_rate.rename(columns={'DGS1':'rate'})
df_1yr_rate = df_1yr_rate[['settle_date','rate']]
df_1yr_rate.rate = [0.0 if s=='.' else float(s) / 100 for s in df_1yr_rate.rate]
df_1yr_rate['prev'] = df_1yr_rate.rate.rolling(5).mean()
df_1yr_rate.rate = df_1yr_rate.apply(lambda r:r.prev if r.rate==0 else r.rate,axis=1)
df_div = pd.read_csv('sp_div_yield.csv')

2020-05-25 13:46:32,633 - urllib3.connectionpool - DEBUG - Starting new HTTPS connection (1): finance.yahoo.com:443
2020-05-25 13:46:33,387 - urllib3.connectionpool - DEBUG - https://finance.yahoo.com:443 "GET /quote/%5EGSPC/history?period1=643671979&period2=1590479999&interval=1d&frequency=1d&filter=history HTTP/1.1" 200 None
2020-05-25 13:46:33,804 - urllib3.connectionpool - DEBUG - Starting new HTTPS connection (1): finance.yahoo.com:443
2020-05-25 13:46:34,310 - urllib3.connectionpool - DEBUG - https://finance.yahoo.com:443 "GET /quote/%5EVIX/history?period1=643671979&period2=1590479999&interval=1d&frequency=1d&filter=history HTTP/1.1" 200 None
2020-05-25 13:46:34,667 - urllib3.connectionpool - DEBUG - Starting new HTTPS connection (1): finance.yahoo.com:443
2020-05-25 13:46:35,212 - urllib3.connectionpool - DEBUG - https://finance.yahoo.com:443 "GET /quote/%5ETNX/history?period1=643671979&period2=1590479999&interval=1d&frequency=1d&filter=history HTTP/1.1" 200 None


### Calculate the cost/revenue of the hedge.
The put hedge that you will buy will initially be below the current SP price by a percentage which you set in the variable ```put_perc_otm```.  When the price of the SP rises high enough so that you can raise the strike price of the hedge, you sell the current put (if there is any value in it) and buy a new put that is ```put_perc_otm``` percent higher than the previous put.  In this way, you are not letting your hedge get too far from the money.


* Remember that, since you are comparing this put strategy to "Buy-And-Hold"
  * Rolls to a higher strike are a cost to the strategy
  * Rolls to a lower strike are revenue to the strategy.

## This the main step.
#### Step 04: create the dataframe called ```dft``` which has all of the strategy info, incluing hedge values.



In [9]:
def calc_put_spread(
    atm_vol,current_hedge_strike,prev_hedge_strike,hedge_date,prev_hedge_date,rate):
    '''
    !! This should only be exexuted on rows of dft where dft.time_to_hedge==True !!

    Calculate the value of the option spread where the legs are: 
      1. the current_hedge_strike 
      2. previous hedge strike
    The value will be positive if you are buying the spread b/c you are rolling
      the previous hedge forward (to a higher strike).
    The value will be negative if you are selling the spread b/c you are rolling
      the previous hedge backward (to a lower strike)
    '''
     #black.black(flag, F, K, t, r, sigma)
    atm_vol = atm_vol
    if (np.isnan(prev_hedge_strike)) or (prev_hedge_strike < current_hedge_strike):
        curr_strike_vol = atm_vol + .04 
        prev_strike_vol = atm_vol + .08
    else:
        curr_strike_vol = atm_vol - .04 
        prev_strike_vol = atm_vol - .06

    days_left_in_prev_hedge = (hedge_date - prev_hedge_date).days

    # calculate remaining of previous hedge
    if np.isnan(prev_hedge_strike):
        underlying_price = current_hedge_strike * (1+put_perc_otm)
        curr_hedge =  black.black('p', underlying_price, current_hedge_strike, years_to_hedge,rate, curr_strike_vol)
        remaining_opt_value = 0
    elif prev_hedge_strike < current_hedge_strike:
        # we are rolling up b/c the market is put_perc_otm ABOVE the current_hedge
        underlying_price = current_hedge_strike * (1+put_perc_otm)
        curr_hedge =  black.black('p', underlying_price, current_hedge_strike, years_to_hedge,rate, curr_strike_vol)
        if days_left_in_prev_hedge > years_to_hedge*365:
            remaining_opt_value = 0
        else:
            time_remaining = days_left_in_prev_hedge/(years_to_hedge*365)
            remaining_opt_value = black.black('p', underlying_price, prev_hedge_strike, 
                                              time_remaining, rate, prev_strike_vol)
    else:
        # we are rolling down b/c the market is put_perc_otm BELOW the current_hedge
        underlying_price = current_hedge_strike * (1-put_perc_otm)
        curr_hedge =  black.black('p', underlying_price, current_hedge_strike, years_to_hedge, rate, curr_strike_vol)
        if days_left_in_prev_hedge > years_to_hedge*365:
            remaining_opt_value = prev_hedge_strike - underlying_price
        else:
            remaining_opt_value =  black.black('p', underlying_price, prev_hedge_strike, years_to_hedge, rate, prev_strike_vol)


    return curr_hedge - remaining_opt_value


In [113]:
# %%time
# yyyymmdd_beg = 19900101
# yyyymmdd_end = 20200525
# put_perc_otm = .14
# years_to_hedge = 1

# # Create a lambda that converts yyyymmdd integer to a datetime object
# yyyymmdd_to_dt = lambda v:datetime.datetime(
#         int(str(v)[0:4]),int(str(v)[4:6]),int(str(v)[6:8])
# )

# # Grab only the relevant columns from df_spy
# dft = df_spy[['settle_date','close','high','low']]
# if yyyymmdd_beg is not None:
#     dft = dft[dft.settle_date>=yyyymmdd_beg]
# if yyyymmdd_end is not None:
#     dft = dft[dft.settle_date<=yyyymmdd_end]

# # Create a datetime settle date, along with the yyyymmdd settle_date column
# dft['settle_dt'] = dft.settle_date.apply(yyyymmdd_to_dt)
# #     print(f"create_dft inputs:{put_perc_otm,years_to_hedge,yyyymmdd_beg,yyyymmdd_end}")
# # Initialize currrent_strike, which is below the money
# current_long_price = dft.iloc[0].close
# current_strike = current_long_price * (1 - put_perc_otm)
# current_strike_array = [current_strike]

# # Create an array of high and low values, to speed up loop processing    
# m = dft[['high','low']].values

# # Loop here to determine the hedge strikes
# for i in range(1,len(m)):
#     # Get high and low
#     curr_high = m[i][0]
#     curr_low = m[i][1]
#     # If the price rises past current_strike * (1 + put_perc_otm) * (1+ put_perc_otm)
#     #   then you want to roll the put strike up,essentially BUYING a put spread
#     if curr_high  >= current_strike * (1 + put_perc_otm)**2:
#         # roll strikes up, like buying put spreads as market goes up
#         current_strike = current_strike * (1 + put_perc_otm)
#     # If the price falls below current_strike * (1 - put_perc_otm) * (1- put_perc_otm)
#     #   then you want to roll the put strike down, essentially SELLING a put spread
#     elif curr_low <= current_strike * (1 - put_perc_otm)**2:
#         # Roll strikes down (like selling put spreads as market drops)
#         current_strike = current_strike * (1 - put_perc_otm)
#     # Accumulate the current_strike (it either remained unchanged, went up, or went down)
#     current_strike_array.append(current_strike)

# # Update dft with the current_strike array    
# dft['current_hedge_strike'] = current_strike_array
# # Create previous strike, so that you can tell when you have to buy or sell
# #   put spreads to roll your hedge to a new higher or lower level.
# dft['prev_hedge_strike'] = dft.current_hedge_strike.shift(1)

# # The next 2 lines are where you determine the dates on which you execute hedges
# dft.loc[dft.prev_hedge_strike!=dft.current_hedge_strike,'time_to_hedge'] = True
# dft.loc[dft.prev_hedge_strike==dft.current_hedge_strike,'time_to_hedge'] = False

# # On the next 4 rows, create the hedge_date, which will be used for calculating put prices.
# dft.loc[dft.time_to_hedge,'hedge_date'] = dft.loc[dft.time_to_hedge].settle_date
# #      Give all rows of dft that are NOT rows where time_to_hedge == True a value of the min settle_date
# dft.loc[dft.time_to_hedge==False,'hedge_date'] = dft.settle_date.min()
# #      This expanding command will make each row's hedge_date either the last hedge_date, or a new hedge_date
# dft.hedge_date = dft.hedge_date.expanding(min_periods=1).max()
# #      Now make the hedge_date a datetime object
# dft.hedge_date = dft.hedge_date.apply(yyyymmdd_to_dt)

# # Create days_of_hedge, which will give you the total days that the hedge was on
# dft['prev_hedge_date'] = dft.hedge_date.shift(1)
# dft['days_of_hedge'] = (dft.settle_dt - dft.hedge_date).dt.days        
# dft.loc[dft.time_to_hedge,'days_of_hedge'] = (dft[dft.time_to_hedge].hedge_date - dft[dft.time_to_hedge].prev_hedge_date).dt.days

# # Obtain atm_vol from the VIX
# df_vix2 = df_vix[['settle_date','close']]
# df_vix2 = df_vix2.rename(columns={'close':'atm_vol'})
# df_vix2.atm_vol = df_vix2.atm_vol / 100
# dft = dft.merge(df_vix2,on='settle_date',how='inner')

# # Obtain interest rates fro the 1 year treasury rate
# dft = dft.merge(df_1yr_rate,on='settle_date',how='inner')

# # Obtain the divident yield from the SP dividend yield dataframe
# dft['year'] = dft.settle_date.apply(lambda v:int(str(v)[0:4]))
# dft = dft.merge(df_div,on='year',how='inner')

# # Now calculate cost/revenue of buying put spreads, or selling put spreads
# def _calc_put_spread(r):
#     return calc_put_spread(
#         r.atm_vol,r.current_hedge_strike,r.prev_hedge_strike,
#         r.hedge_date,r.prev_hedge_date,r.rate)
# dft.loc[dft.time_to_hedge,'hedge'] = dft.loc[dft.time_to_hedge].apply(_calc_put_spread,axis=1)
# dft.loc[dft.time_to_hedge==False,'hedge'] = 0
# dft['hedge_cumulative'] = [0] + dft.iloc[1:].hedge.cumsum().values.tolist()


# # dft['hedged_value'] = dft.apply(lambda r:max(r.current_hedge_strike,r.close) - r.hedge_cumulative,axis=1)
# # dft['prev_hedged_value'] = dft.hedged_value.shift(1)
# # dft['hedged_daily_return'] = dft.apply(lambda r:r.hedged_value/r.prev_hedged_value-1,axis=1)
# # dft['prev_close'] = dft.close.shift(1)
# # dft['unhedged_return']  = dft.apply(lambda r:r.close/r.prev_close-1,axis=1)    

# dft['hedged_value'] = np.maximum(dft.current_hedge_strike.values,dft.close.values) - dft.hedge_cumulative.values
# dft['prev_hedged_value'] = dft.hedged_value.shift(1)
# dft['hedged_daily_return'] = dft.hedged_value/dft.prev_hedged_value-1
# dft['prev_close'] = dft.close.shift(1)
# dft['unhedged_return']  = dft.close/dft.prev_close-1






CPU times: user 122 ms, sys: 3.24 ms, total: 126 ms
Wall time: 124 ms


In [111]:
np.maximum(np.array([1,2,3,4]),np.array([1,3,2,5])) - np.array([1,1,1,1])

array([0, 2, 2, 4])

In [121]:
def create_dft(put_perc_otm,years_to_hedge,
              yyyymmdd_beg=None,yyyymmdd_end=None,use_fast=True):
    # Create a lambda that converts yyyymmdd integer to a datetime object
    yyyymmdd_to_dt = lambda v:datetime.datetime(
            int(str(v)[0:4]),int(str(v)[4:6]),int(str(v)[6:8])
    )

    # Grab only the relevant columns from df_spy
    dft = df_spy[['settle_date','close','high','low']]
    if yyyymmdd_beg is not None:
        dft = dft[dft.settle_date>=yyyymmdd_beg]
    if yyyymmdd_end is not None:
        dft = dft[dft.settle_date<=yyyymmdd_end]
        
    # Create a datetime settle date, along with the yyyymmdd settle_date column
    dft['settle_dt'] = dft.settle_date.apply(yyyymmdd_to_dt)
#     print(f"create_dft inputs:{put_perc_otm,years_to_hedge,yyyymmdd_beg,yyyymmdd_end}")
    # Initialize currrent_strike, which is below the money
    current_long_price = dft.iloc[0].close
    current_strike = current_long_price * (1 - put_perc_otm)
    current_strike_array = [current_strike]

    # Create an array of high and low values, to speed up loop processing    
    m = dft[['high','low']].values

    # Loop here to determine the hedge strikes
    for i in range(1,len(m)):
        # Get high and low
        curr_high = m[i][0]
        curr_low = m[i][1]
        # If the price rises past current_strike * (1 + put_perc_otm) * (1+ put_perc_otm)
        #   then you want to roll the put strike up,essentially BUYING a put spread
        if curr_high  >= current_strike * (1 + put_perc_otm)**2:
            # roll strikes up, like buying put spreads as market goes up
            current_strike = current_strike * (1 + put_perc_otm)
        # If the price falls below current_strike * (1 - put_perc_otm) * (1- put_perc_otm)
        #   then you want to roll the put strike down, essentially SELLING a put spread
        elif curr_low <= current_strike * (1 - put_perc_otm)**2:
            # Roll strikes down (like selling put spreads as market drops)
            current_strike = current_strike * (1 - put_perc_otm)
        # Accumulate the current_strike (it either remained unchanged, went up, or went down)
        current_strike_array.append(current_strike)

    # Update dft with the current_strike array    
    dft['current_hedge_strike'] = current_strike_array
    # Create previous strike, so that you can tell when you have to buy or sell
    #   put spreads to roll your hedge to a new higher or lower level.
    dft['prev_hedge_strike'] = dft.current_hedge_strike.shift(1)
    
    # The next 2 lines are where you determine the dates on which you execute hedges
    dft.loc[dft.prev_hedge_strike!=dft.current_hedge_strike,'time_to_hedge'] = True
    dft.loc[dft.prev_hedge_strike==dft.current_hedge_strike,'time_to_hedge'] = False

    # On the next 4 rows, create the hedge_date, which will be used for calculating put prices.
    dft.loc[dft.time_to_hedge,'hedge_date'] = dft.loc[dft.time_to_hedge].settle_date
    #      Give all rows of dft that are NOT rows where time_to_hedge == True a value of the min settle_date
    dft.loc[dft.time_to_hedge==False,'hedge_date'] = dft.settle_date.min()
    #      This expanding command will make each row's hedge_date either the last hedge_date, or a new hedge_date
    dft.hedge_date = dft.hedge_date.expanding(min_periods=1).max()
    #      Now make the hedge_date a datetime object
    dft.hedge_date = dft.hedge_date.apply(yyyymmdd_to_dt)
    
    # Create days_of_hedge, which will give you the total days that the hedge was on
    dft['prev_hedge_date'] = dft.hedge_date.shift(1)
    dft['days_of_hedge'] = (dft.settle_dt - dft.hedge_date).dt.days        
    dft.loc[dft.time_to_hedge,'days_of_hedge'] = (dft[dft.time_to_hedge].hedge_date - dft[dft.time_to_hedge].prev_hedge_date).dt.days

    # Obtain atm_vol from the VIX
    df_vix2 = df_vix[['settle_date','close']]
    df_vix2 = df_vix2.rename(columns={'close':'atm_vol'})
    df_vix2.atm_vol = df_vix2.atm_vol / 100
    dft = dft.merge(df_vix2,on='settle_date',how='inner')

    # Obtain interest rates fro the 1 year treasury rate
    dft = dft.merge(df_1yr_rate,on='settle_date',how='inner')

    # Obtain the divident yield from the SP dividend yield dataframe
    dft['year'] = dft.settle_date.apply(lambda v:int(str(v)[0:4]))
    dft = dft.merge(df_div,on='year',how='inner')

    # Now calculate cost/revenue of buying put spreads, or selling put spreads
    def _calc_put_spread(r):
        return calc_put_spread(
            r.atm_vol,r.current_hedge_strike,r.prev_hedge_strike,
            r.hedge_date,r.prev_hedge_date,r.rate)
    dft.loc[dft.time_to_hedge,'hedge'] = dft.loc[dft.time_to_hedge].apply(_calc_put_spread,axis=1)
    dft.loc[dft.time_to_hedge==False,'hedge'] = 0
    dft['hedge_cumulative'] = [0] + dft.iloc[1:].hedge.cumsum().values.tolist()

    if use_fast:
        dft['hedged_value'] = np.maximum(dft.current_hedge_strike.values,dft.close.values) - dft.hedge_cumulative.values
        dft['prev_hedged_value'] = dft.hedged_value.shift(1)
        dft['hedged_daily_return'] = dft.hedged_value/dft.prev_hedged_value-1
        dft['prev_close'] = dft.close.shift(1)
        dft['unhedged_return']  = dft.close/dft.prev_close-1
    else:
        dft['hedged_value'] = dft.apply(lambda r:max(r.current_hedge_strike,r.close) - r.hedge_cumulative,axis=1)
        dft['prev_hedged_value'] = dft.hedged_value.shift(1)
        dft['hedged_daily_return'] = dft.apply(lambda r:r.hedged_value/r.prev_hedged_value-1,axis=1)
        dft['prev_close'] = dft.close.shift(1)
        dft['unhedged_return']  = dft.apply(lambda r:r.close/r.prev_close-1,axis=1) 
    
    
    # Return dft
    return dft

### Test ```create_dft``` and ```create_put_spread```

In [120]:
%time dft = create_dft(.125,1,yyyymmdd_beg=19900101,yyyymmdd_end=20200520)
dft.query('time_to_hedge==True').iloc[1:].hedged_daily_return.sum()
#-0.7151059829495886

CPU times: user 132 ms, sys: 4.34 ms, total: 137 ms
Wall time: 136 ms


-0.7151059829495886

In [21]:
r=dft.query('time_to_hedge==True').iloc[0]
display.display(r)
calc_put_spread(
            r.atm_vol,r.current_hedge_strike,r.prev_hedge_strike,
            r.hedge_date,r.prev_hedge_date,r.rate)


settle_date                        20190102
close                               2510.03
high                                2519.49
low                                 2467.47
settle_dt               2019-01-02 00:00:00
current_hedge_strike                2196.28
prev_hedge_strike                       NaN
time_to_hedge                          True
hedge_date              2019-01-02 00:00:00
prev_hedge_date                         NaT
days_of_hedge                           NaN
atm_vol                              0.2322
rate                                  0.026
prev                                0.02076
year                                   2019
div_yield                            0.0182
hedge                                213.82
hedge_cumulative                          0
hedged_value                        2510.03
prev_hedged_value                       NaN
hedged_daily_return                     NaN
prev_close                              NaN
unhedged_return                 

213.81992467787535

#### Step 05: graph the close of ^GSCP (SP 500) vs the strikes at which we hedged

In [122]:
dft = create_dft(put_perc_otm,years_to_hedge)
dft_to_plot = dft[['settle_date','close','current_hedge_strike']]
# iplot(plotly_plot(df_in=dft_to_plot,x_column='settle_date'))
f = plotly_plot(df_in=dft_to_plot,x_column='settle_date',plot_title="Close vs Current Hedge Strike")
f.show(config={'displayModeBar':True})

#### Step 06: list all put purchases when rolling to a higher strike as the market rises.
You are essentially buying a put spread on every roll higher.

In [123]:
dft[(dft.time_to_hedge) & (dft.prev_hedge_strike<dft.current_hedge_strike)]

settle_date        close         high          low  settle_dt  \
318      19910828   396.640015   396.640015   393.049988 1991-08-28   
703      19930308   454.709991   454.709991   446.119995 1993-03-08   
1245     19950428   514.710022   515.289978   510.899994 1995-04-28   
1352     19950929   584.409973   587.609985   584.000000 1995-09-29   
1510     19960515   665.419983   669.820007   664.460022 1996-05-15   
1678     19970114   768.859985   772.039978   759.510010 1997-01-14   
1780     19970610   865.270020   870.049988   862.179993 1997-06-10   
1941     19980129   985.489990   992.650024   975.210022 1998-01-29   
1987     19980406  1121.380005  1131.989990  1121.369995 1998-04-06   
2219     19990309  1279.839966  1293.739990  1275.109985 1999-03-09   
2425     19991230  1464.469971  1473.099976  1462.599976 1999-12-30   
3826     20050728  1243.719971  1245.150024  1235.810059 2005-07-28   
4168     20061205  1414.760010  1415.270020  1408.780029 2006-12-05   
4850     20090821  1026.130005  1027.589966  1009.059998 2009-08-21   
4992     20100317  1166.209961  1169.839966  1159.939941 2010-03-17   
5222     20110211  1329.150024  1330.790039  1316.079956 2011-02-11   
5722     20130208  1517.930054  1518.310059  1509.390015 2013-02-08   
5875     20130918  1725.520020  1729.439941  1700.349976 2013-09-18   
6072     20140701  1973.319946  1978.579956  1962.290039 2014-07-01   
6688     20161208  2246.189941  2251.689941  2237.570068 2016-12-08   
6904     20171018  2561.260010  2564.110107  2559.669922 2017-10-18   
7136     20180920  2930.750000  2934.800049  2919.729980 2018-09-20   
7469     20200117  3329.620117  3329.879883  3318.860107 2020-01-17   

      current_hedge_strike  prev_hedge_strike time_to_hedge hedge_date  \
318             347.630219         304.938788          True 1991-08-28   
703             396.298449         347.630219          True 1993-03-08   
1245            451.780232         396.298449          True 1995-04-28   
1352            515.029465         451.780232          True 1995-09-29   
1510            587.133590         515.029465          True 1996-05-15   
1678            669.332293         587.133590          True 1997-01-14   
1780            763.038814         669.332293          True 1997-06-10   
1941            869.864248         763.038814          True 1998-01-29   
1987            991.645242         869.864248          True 1998-04-06   
2219           1130.475576         991.645242          True 1999-03-09   
2425           1288.742157        1130.475576          True 1999-12-30   
3826           1086.595217         953.153699          True 2005-07-28   
4168           1238.718547        1086.595217          True 2006-12-05   
4850            898.199575         787.894364          True 2009-08-21   
4992           1023.947516         898.199575          True 2010-03-17   
5222           1167.300168        1023.947516          True 2011-02-11   
5722           1330.722192        1167.300168          True 2013-02-08   
5875           1517.023299        1330.722192          True 2013-09-18   
6072           1729.406560        1517.023299          True 2014-07-01   
6688           1971.523479        1729.406560          True 2016-12-08   
6904           2247.536766        1971.523479          True 2017-10-18   
7136           2562.191913        2247.536766          True 2018-09-20   
7469           2920.898781        2562.191913          True 2020-01-17   

     prev_hedge_date  ...     prev  year  div_yield      hedge  \
318       1990-05-25  ...  0.05762  1991     0.0311  10.005256   
703       1991-08-28  ...  0.03318  1993     0.0272  12.856264   
1245      1993-03-08  ...  0.06238  1995     0.0230   8.086273   
1352      1995-04-28  ...  0.05688  1995     0.0230  10.093529   
1510      1995-09-29  ...  0.05616  1996     0.0201  13.589386   
1678      1996-05-15  ...  0.05620  1997     0.0160  19.604015   
1780      1997-01-14  ...  0.05748  1997     0.0160  27.817858

#### Step 08: list all put purchases when rolling to a lower strike.
In this case, you are selling put spreads.

In [124]:
dft[(dft.time_to_hedge) & (dft.prev_hedge_strike>dft.current_hedge_strike)]

settle_date       close         high         low  settle_dt  \
2857     20010921  965.799988   984.539978  944.750000 2001-09-21   
3065     20020722  819.849976   854.130005  813.260010 2002-07-22   
4632     20081009  909.919983  1005.250000  909.190002 2008-10-09   
4662     20081120  752.440002   820.520020  747.780029 2008-11-20   
4733     20090306  683.380005   699.090027  666.789978 2009-03-06   

      current_hedge_strike  prev_hedge_strike time_to_hedge hedge_date  \
2857           1108.318255        1288.742157          True 2001-09-21   
3065            953.153699        1108.318255          True 2002-07-22   
4632           1065.297951        1238.718547          True 2008-10-09   
4662            916.156238        1065.297951          True 2008-11-20   
4733            787.894364         916.156238          True 2009-03-06   

     prev_hedge_date  ...     prev  year  div_yield       hedge  \
2857      1999-12-30  ...  0.02598  2001     0.0137  -94.498804   
3065      2001-09-21  ...  0.01962  2002     0.0181 -114.100561   
4632      2006-12-05  ...  0.01304  2008     0.0315  -11.701159   
4662      2008-10-09  ...  0.01022  2008     0.0315 -104.915940   
4733      2008-11-20  ...  0.00678  2009     0.0197  -92.791772   

      hedge_cumulative  hedged_value  prev_hedged_value  hedged_daily_return  \
2857        162.956555    945.361700        1031.286798            -0.083318   
3065         48.855994    904.297705         945.361700            -0.043437   
4632         74.166889    991.131061        1152.850499            -0.140278   
4662        -30.749051    946.905288         991.131061            -0.044622   
4733       -123.540823    911.435187         946.905288            -0.037459   

      prev_close  unhedged_return  
2857  984.539978        -0.019034  
3065  847.750000        -0.032911  
4632  984.940002        -0.076167  
4662  806.580017        -0.067123  
4733  682.549988         0.001216  

[5 rows x 23 columns]

#### Step 09: plot the dramatic roll down cases during 2008-2010

In [125]:
dft_to_plot = dft[['settle_date','close','current_hedge_strike']]
dft_to_plot = dft_to_plot[(dft_to_plot.settle_date>=20080501)]

iplot(plotly_plot(df_in=dft_to_plot,x_column='settle_date',
                 plot_title="Close vs Current Hedge Strike",modebar_orientation='h'))

#### Step 10: show comparative PL's

In [126]:
dft.columns.values

array(['settle_date', 'close', 'high', 'low', 'settle_dt',
       'current_hedge_strike', 'prev_hedge_strike', 'time_to_hedge',
       'hedge_date', 'prev_hedge_date', 'days_of_hedge', 'atm_vol',
       'rate', 'prev', 'year', 'div_yield', 'hedge', 'hedge_cumulative',
       'hedged_value', 'prev_hedged_value', 'hedged_daily_return',
       'prev_close', 'unhedged_return'], dtype=object)

In [127]:
# dft['hedged_value'] = dft.apply(lambda r:max(r.current_hedge_strike,r.close) - r.hedge_cumulative,axis=1)
# dft['prev_hedged_value'] = dft.hedged_value.shift(1)
# dft['hedged_daily_return'] = dft.apply(lambda r:r.hedged_value/r.prev_hedged_value-1,axis=1)
# dft['prev_close'] = dft.close.shift(1)
# dft['unhedged_return']  = dft.apply(lambda r:r.close/r.prev_close-1,axis=1)

In [128]:
hdrm = dft[dft.hedged_daily_return!=0].hedged_daily_return.mean()
hdrs = dft.hedged_daily_return[dft.hedged_daily_return!=0].std()
udrm = dft.unhedged_return.mean()
udrs = dft.unhedged_return.std()

hdrm*256**.5,udrm*256**.5,hdrm/hdrs*256**.5,udrm/udrs*256**.5

(0.005569920664669999,
 0.0055478344844238445,
 0.5496565484896815,
 0.4820352727776615)

In [129]:
dft.hedged_daily_return.std()*256**.5,dft.unhedged_return.std()*256**.5

(0.1548984687277567, 0.184147004926182)

In [130]:
def create_comparative_returns(dft,years_to_hedge,rebal_target,rebal_adjust,pom=put_perc_otm):
    ret = {}
    
    # Get the begin and end values of dft.close, using the lowest and highest dates
    row_min = dft[dft.settle_dt == dft.settle_dt.min()].iloc[0]
    row_max = dft[dft.settle_dt == dft.settle_dt.max()].iloc[0]
    years_of_position = (row_max.settle_dt - row_min.settle_dt).days/365
    beg_value = row_min.close
    curr_value  = row_max.close
    
    # Caculate various returns
    #   return not hedged
    curr_return  = (curr_value/beg_value)**(1/years_of_position) - 1
    #   return as of the date of the highest high
    highest_high_value = dft[dft.high==dft.high.max()].iloc[0].close
    highest_return_no_hedge = (highest_high_value/beg_value)**(1/years_of_position) - 1

    #   current return if you hedged
    hedge_cost = dft[dft.time_to_hedge].hedge.sum()
    hedged_value = max(row_max.current_hedge_strike,curr_value) - hedge_cost
    hedged_return = (hedged_value/beg_value)**(1/years_of_position) - 1

    # Calculate the return from a portfolio that is rebalanced when the portfolio's
    #     percentage of stock reaches some threshold.
    
    # Get the initial shares of stock and cash
    shares = rebal_target / dft.close[0]
    cash = 1 - rebal_target
    # Set up arrays to accumlate daily changes
    cash_per_day = []
    stock_per_day = []
    port_per_day = []
    prices = dft.close.values
    dates = dft.settle_date.values
    cash_rates = dft.rate.values / 365
    rebal_dates = []
    rebal_sales = []
    stock_percs = []

    # Main loop to determine portfolio values over time, and to determine when to rebalance
    for i in range(1,len(dft)):
        # Calculate current stock dollars
        stock_dollars = shares * prices[i]
        # have your cash earn interest each day
        cash_rate = cash_rates[i]
        cash = cash * (1+cash_rate)
        # determine portfolio value 
        port = stock_dollars + cash
        # determine pre-rebalance stock percent
        stock_perc = stock_dollars/port
        stock_percs.append(stock_perc)
        # determine if you should rebalance
        if stock_perc >= rebal_adjust:
            # do re-balance
            dollars_to_sell = stock_dollars - rebal_target*port
            new_stock_dollars = stock_dollars - dollars_to_sell
            new_cash = cash + dollars_to_sell
            new_port = new_stock_dollars + new_cash
            shares = new_stock_dollars/prices[i]
            cash = new_cash
            stock_dollars = new_stock_dollars
            rebal_dates.append(dates[i])
            rebal_sales.append(dollars_to_sell)
        cash_per_day.append(cash)
        stock_per_day.append(stock_dollars)
        port_per_day.append(cash+stock_dollars)    
    
    df_daily_values = pd.DataFrame({
        'cash_per_day':cash_per_day,
        'stock_per_day':stock_per_day,
        'port_per_day':port_per_day,
        'close':prices[1:],
        'date':dates[1:],
        'cash_rate':cash_rates[1:],
        'stock_perc':stock_percs
    })
    df_rebalance_info = pd.DataFrame({
        'rebal_date':rebal_dates,
        'rebal_sale':rebal_sales,
    })
    # get total years and calculate annualized portfolio performance
    total_days = (dft.settle_dt.values[-1] - dft.settle_dt.values[0]).astype('timedelta64[D]')// np.timedelta64(1, 'D')
    total_years = total_days / 365
    end_port_value = port_per_day[-1]
    beg_port_value = port_per_day[0]
    annualized_port_yield = round((end_port_value/beg_port_value)**(1/total_years) - 1,3)
#     annualized_std = 
    df_values = pd.DataFrame({
        'return_type':['total years','annualized current return',
                       f'annualized highest return',f'annualized current hedged return {round(pom*100,1)}%',
                      f'rebalanced ({int(rebal_target*100)}%,{int(rebal_adjust*100)}%) portfolio end value'],
        'current_value':[total_years,curr_value,highest_high_value,hedged_value,end_port_value],
        'return':[0,curr_return,highest_return_no_hedge,hedged_return,annualized_port_yield]})
    return df_values,df_daily_values,df_rebalance_info


In [140]:
dft3 = create_dft(.14,1,yyyymmdd_beg=20190101,yyyymmdd_end=20200520)
create_comparative_returns(dft3,years_to_hedge,rebal_target,rebal_adjust,pom=put_perc_otm)[0]

return_type  current_value    return
0                               total years       1.380822  0.000000
1                 annualized current return    2971.610107  0.130040
2                 annualized highest return    3386.149902  0.242129
3    annualized current hedged return 14.0%    2738.273890  0.065059
4  rebalanced (60%,70%) portfolio end value       1.116802  0.095000

#### Step 11: Calculate returns from a portfolio that holds a ratio of stock and 1 year treasury bonds
(*When you rebalance the portfolio after it achieves a certain threshold*)


In [132]:
dft.tail()

settle_date        close         high          low  settle_dt  \
7551     20200515  2863.699951  2865.010010  2816.780029 2020-05-15   
7552     20200518  2953.909912  2968.090088  2913.860107 2020-05-18   
7553     20200519  2922.939941  2964.209961  2922.350098 2020-05-19   
7554     20200520  2971.610107  2980.290039  2953.629883 2020-05-20   
7555     20200521  2948.510010  2978.500000  2938.570068 2020-05-21   

      current_hedge_strike  prev_hedge_strike time_to_hedge hedge_date  \
7551           2920.898781        2920.898781         False 2020-01-17   
7552           2920.898781        2920.898781         False 2020-01-17   
7553           2920.898781        2920.898781         False 2020-01-17   
7554           2920.898781        2920.898781         False 2020-01-17   
7555           2920.898781        2920.898781         False 2020-01-17   

     prev_hedge_date  ...     prev  year  div_yield  hedge  hedge_cumulative  \
7551      2020-01-17  ...  0.00154  2020       0.02    0.0        209.892801   
7552      2020-01-17  ...  0.00156  2020       0.02    0.0        209.892801   
7553      2020-01-17  ...  0.00156  2020       0.02    0.0        209.892801   
7554      2020-01-17  ...  0.00158  2020       0.02    0.0        209.892801   
7555      2020-01-17  ...  0.00160  2020       0.02    0.0        209.892801   

      hedged_value  prev_hedged_value  hedged_daily_return   prev_close  \
7551   2711.005979        2711.005979             0.000000  2852.500000   
7552   2744.017111        2711.005979             0.012177  2863.699951   
7553   2713.047140        2744.017111            -0.011286  2953.909912   
7554   2761.717306        2713.047140             0.017939  2922.939941   
7555   2738.617208        2761.717306            -0.008364  2971.610107   

      unhedged_return  
7551         0.003926  
7552         0.031501  
7553        -0.010484  
7554         0.016651  
7555        -0.007774  

[5 rows x 23 columns]

### Display results of portfolio analysis above, comparing:
1. Annualized Returns from 100% long
2. Highest Historical Return from 100% long
3. Annualized Return of put strategy portfolio
4. Annualized Return of rebalanced portfolio

In [133]:
iplot(plotly_plot(df_in=dft[['settle_date','close']],x_column='settle_date'))


In [134]:
STYLE_TITLE={
    'line-height': '20px',
    'textAlign': 'center',
    'background-color':'#47bacc',
    'color':'#FFFFF9',
    'vertical-align':'middle',
    'horizontal-align':'middle',
} 



### Create methods to convert input strings of:
1. beg_date in format yyyy-mm-dd (e.g. 1990-01-02 for Jan 2nd, 1990)
2. beg_date in format yyyy-mm-dd (e.g. 1990-01-02 for Jan 2nd, 1990)
3. put percent out of the money as decimal (e.g .14 for 14% out of the money)

#### into DataFrames and Graph Figures


In [306]:
def yyyymmdd_to_dt_string(yyyymmdd_int):
    y = str(yyyymmdd_int)[0:4]
    mn = str(yyyymmdd_int)[4:6]
    d = str(yyyymmdd_int)[6:8]
    return f"{y}-{mn}-{d}"

def _get_df_values_from_input_data(input_data):
    print(f"_get_df_values_from_input_data input_data: {input_data}")
    bd = input_data[0]
    ed = input_data[1]
    perc_otm_string = input_data[2]
    rebal_target_string = input_data[3]
    rebal_adjust_string = input_data[4]
    yyyymmdd_beg = int(bd[0:4])*100*100 + int(bd[5:7])*100 + int(bd[8:10])
    yyyymmdd_end = int(ed[0:4])*100*100 + int(ed[5:7])*100 + int(ed[8:10])
    new_pom = float(perc_otm_string)
    new_rebal_target = float(rebal_target_string)
    new_rebal_adjust = float(rebal_adjust_string)
    return _get_df_values(yyyymmdd_beg,yyyymmdd_end,new_pom,new_rebal_target,new_rebal_adjust)

def _get_df_values(yyyymmdd_beg,yyyymmdd_end,pom,rebal_target,rebal_adjust):
    # validate values
    new_pom = pom
    new_rebal_target = rebal_target
    new_rebal_adjust = rebal_adjust
    dft_new = create_dft(new_pom,years_to_hedge,
                       yyyymmdd_beg=yyyymmdd_beg,yyyymmdd_end=yyyymmdd_end)

    df_values,df_daily_values,df_rebalance_info = create_comparative_returns(
        dft_new,years_to_hedge,new_rebal_target,new_rebal_adjust,pom=new_pom)
    df_values.current_value = df_values.current_value.round(3) 
    df_values['return'] = df_values['return'].round(3) 
    return dft_new,df_values,df_daily_values,df_rebalance_info

def _get_graph_stock_vs_cash_figure(input_data):
    dft_new,df_values,df_daily_values,_ = _get_df_values_from_input_data(input_data)

    stock_percs = df_daily_values.stock_perc.values
    dates =  df_daily_values.date.values
    port_per_day = df_daily_values.port_per_day.values
    df_stock_perc = pd.DataFrame(
        {'dt':dates,'stock perc':stock_percs,
        '1 Dollar':port_per_day})

    annualized_port_yield = df_values['return'].values[4]    
    title = f"""Percent Stock<br>vs<br>Portfolio Value."""
    port_values_fig = plotly_plot(
        df_in=df_stock_perc,x_column='dt',yaxis2_cols=['1 Dollar'],
        plot_title=title,
        y_left_label='Percent of Portfolio in Stock',
        y_right_label='Value of 1 Portfolio Dollar',width=700,height=300,
        number_of_ticks_display=12)
    port_values_fig.update_layout(legend=dict(x=-.1, y=1.2))
    return port_values_fig


def _get_close_vs_hedge_figure(input_data):
    dft_new,_,_,_ = _get_df_values_from_input_data(input_data)
    dft_close_vs_hedge_strike = dft_new[['settle_date','close','current_hedge_strike']]
    dft_close_vs_hedge_strike = dft_close_vs_hedge_strike.rename(columns={'current_hedge_strike':'hedge strike'})
    title2 = f"""Hedge Strike<br>vs<br>SP Closing Price"""    
    fig_graph_close_vs_hedge_strike = plotly_plot(
        df_in=dft_close_vs_hedge_strike,
        x_column='settle_date',
        plot_title=title2,width=700,height=300,
        number_of_ticks_display=12,legend_x=-0.1,legend_y=1.2)
    return fig_graph_close_vs_hedge_strike

def _get_close_vs_hedge_stock_vs_cash_figure(input_data):
    dft_new,df_values,df_daily_values,_ = _get_df_values_from_input_data(input_data)
    df_daily_values['current_hedge_strike'] = dft_new.current_hedge_strike
    names = ['stock_perc','port_per_day','close','current_hedge_strike']
    x_columns = ['date' for _ in range(len(names))]
    yp_rows = [1,1,1,1]
    yp_cols = [1,1,2,2]
    yp_secondary = [False,True,False,False]
    yp_yaxis_titles = ['Stock Percent','Portolio Value','S&P Price / Hedge Strike','S&P Price / Hedge Strike']
    df_yp = pd.DataFrame({'name':names,'x_column':x_columns,
                      'row':yp_rows,'col':yp_cols,'is_secondary':yp_secondary,
                     'yaxis_title':yp_yaxis_titles})
    sp_titles = ['Stock Perc vs Portfolio Value','S&P Price vs Hedge Strike']
    fig =  dashapp.plotly_subplots(df_daily_values,df_yp,title="Portfolio Analysis",
                      num_ticks_to_display=10,subplot_titles=sp_titles) 
    fig = go.Figure(fig)
    fig.update_layout(
        legend=dict(x=-0.1, y=1.4),
        modebar={'orientation': 'v','bgcolor':'grey'}
    )
    return fig

def _get_scenarios_data(input_data):
    beg_year = int(str(input_data[0]))
    end_year = int(str(input_data[1]))
    beg_pom = float(str(input_data[2]))
    end_pom = float(str(input_data[3]))  
    all3_query = f"(year>={beg_year}) and (year<={end_year}) and (pom>={beg_pom}) and (pom<={end_pom})"
    dft_dict = build_scenarios(beg_year,end_year,beg_pom,end_pom,.6,.7)
    df_all3,df_all = build_3d_display_df(dft_dict)
    df_all3_scenarios = df_all3.query(all3_query)
    return [{'df_all3':df_all3_scenarios.to_dict('rows'),'df_all':df_all.to_dict('rows')}]
    
def _get_scenarios_figure_from_data(input_data):
    df_all3_scenarios = pd.DataFrame(input_data[0]['df_all3'])
    fig = px.scatter_3d(df_all3_scenarios, x='pom', y='year', z='ret',color='ret_type')
    fig.update_layout(
        legend=dict(x=-0.1, y=1.2),
        modebar={'orientation': 'v','bgcolor':'grey'}
    )
    return fig


    
def _get_scenarios_figure(input_data):
    beg_year = int(str(input_data[0]))
    end_year = int(str(input_data[1]))
    beg_pom = float(str(input_data[2]))
    end_pom = float(str(input_data[3]))  
    all3_query = f"(year>={beg_year}) and (year<={end_year}) and (pom>={beg_pom}) and (pom<={end_pom})"
    dft_dict = build_scenarios(beg_year,end_year,beg_pom,end_pom,.6,.7)
    df_all3,df_all = build_3d_display_df(dft_dict)
    df_all3_scenarios = df_all3.query(all3_query)
    fig = px.scatter_3d(df_all3_scenarios, x='pom', y='year', z='ret',color='ret_type')
    fig.update_layout(
        legend=dict(x=-0.1, y=1.2),
        modebar={'orientation': 'v','bgcolor':'grey'}
    )
    return fig
    
def make_page_title(title_text,div_id=None,html_container=None,parent_class=None,
                   panel_background_color='#CAE2EB'):
    par_class = parent_class
    if par_class is None:
        par_class = dashapp.pnnm
    htmc = html_container
    if htmc is None:
        htmc = html.H2
        
    title_parts = title_text.split('\n')
    

    title_list = [htmc(tp,className=dashapp.pnncnm) for tp in title_parts]
    r = dashapp.multi_row_panel(title_list,
                 parent_class=par_class,
                 div_id=div_id,
                 panel_background_color=panel_background_color) 
    return r   


In [307]:
inpvals = [str(v) for v in ['1990-01-01','2020-05-21',.14,.6,.7]]
iplot(_get_close_vs_hedge_stock_vs_cash_figure(inpvals))

_get_df_values_from_input_data input_data: ['1990-01-01', '2020-05-21', '0.14', '0.6', '0.7']


In [266]:
dft_new2,df_values2,df_daily_values2,df_rebalance_info2 = _get_df_values(
    19000101,20200521,.14,.6,.7) 
pd.DataFrame({
    'df':['dft_new2','df_values2','df_daily_values2','df_rebalance_info2'],
    'length':[len(dft_new2),len(df_values2),len(df_daily_values2),len(df_rebalance_info2)],
    'cols':[
        ','.join(dft_new2.columns.values),
        ','.join(df_values2.columns.values),
        ','.join(df_daily_values2.columns.values),
        ','.join(df_rebalance_info2.columns.values)]
})

df  length  \
0            dft_new2    7556   
1          df_values2       5   
2    df_daily_values2    7555   
3  df_rebalance_info2       3   

                                                cols  
0  settle_date,close,high,low,settle_dt,current_h...  
1                   return_type,current_value,return  
2  cash_per_day,stock_per_day,port_per_day,close,...  
3                              rebal_date,rebal_sale

### Create scenarios for 3d display of returns vs year, percent out of money (pom), and rebalance percentages


In [147]:
def build_scenarios(beg_year,end_year,low_pom,high_pom,rebal_target,rebal_adust):
    # determine yyyymmdd_end
    dt_now = datetime.datetime.now()
    yyyymmdd_end = end_year*100*100 + 1231
    yyyymmdd_now = dt_to_yyyymmdd(dt_now)
    yyyymmdd_end = min(yyyymmdd_end,yyyymmdd_now)
    # create array of beg_years to loop on
    beg_years = np.arange(beg_year,end_year,1)

    #   loop on increasing beg_year, but holding end_year constant
    dft_dict = {}
    for y in tqdm_notebook(beg_years):
        yyyymmdd_beg = int(y)*100*100 + 101 
        #    loop on pom
        for pom in [round(x,2) for x in np.arange(low_pom,high_pom+.01,.02)]:
            dft_new,df_values,df_daily_values,df_rebalance_info =_get_df_values(
                yyyymmdd_beg,yyyymmdd_end,pom,rebal_target,rebal_adjust)
            dft_dict[(y,pom)] = [dft_new,df_values,df_daily_values,df_rebalance_info] 
    return dft_dict

In [148]:
def build_3d_display_df(dft_dict):
    no_hedge_current =   [a[1].iloc[1]['return'] for a in dft_dict.values()]
    no_hedge_highest =    [a[1].iloc[2]['return'] for a in dft_dict.values()]
    with_hedge_current = [a[1].iloc[3]['return'] for a in dft_dict.values()]
    rebalanced_current =  [a[1].iloc[4]['return'] for a in dft_dict.values()]
    year_pom_array = list(dft_dict.keys())
    year_array = [a[0] for a in year_pom_array]
    pom_array  = [a[1] for a in year_pom_array]
    df_all = pd.DataFrame({
        'year':year_array,
        'pom':pom_array,
        'no_hedge_current':no_hedge_current,
        'no_hedge_highest':no_hedge_highest,
        'with_hedge_current':with_hedge_current,
        'rebalanced_current':rebalanced_current
    })

    df_all2 = df_all[['year','pom','no_hedge_current']].copy()
    df_all2 = df_all2.rename(columns={'no_hedge_current':'ret'})
    df_all2['ret_type'] = 'no_hedge_current'
    df_all2.index = list(range(len(df_all2)))
    for c in ['no_hedge_highest','with_hedge_current','rebalanced_current']:
        df_temp = df_all[['year','pom',c]].copy()
        df_temp.index=list(range(len(df_temp)))
        df_temp = df_temp.rename(columns={c:'ret'})
        df_temp['ret_type'] = c
        df_all2 = df_all2.append(df_temp,ignore_index=True)
        df_all2.index = list(range(len(df_all2)))
    df_all2.ret_type.unique()
    df_all3 = df_all2.query("ret_type in ['with_hedge_current','rebalanced_current']")
    return df_all3,df_all

In [222]:
dft_dict = build_scenarios(1990,2020,.11,.18,.6,.7)
df_all3,df_all = build_3d_display_df(dft_dict)
df_all3

year   pom    ret            ret_type
240  1990  0.11  0.073  with_hedge_current
241  1990  0.13  0.070  with_hedge_current
242  1990  0.15  0.070  with_hedge_current
243  1990  0.17  0.070  with_hedge_current
244  1991  0.11  0.078  with_hedge_current
..    ...   ...    ...                 ...
475  2018  0.17  0.027  rebalanced_current
476  2019  0.11  0.091  rebalanced_current
477  2019  0.13  0.091  rebalanced_current
478  2019  0.15  0.091  rebalanced_current
479  2019  0.17  0.091  rebalanced_current

[240 rows x 4 columns]

In [227]:
dft_dict.keys()

dict_keys([(1990, 0.11), (1990, 0.13), (1990, 0.15), (1990, 0.17), (1991, 0.11), (1991, 0.13), (1991, 0.15), (1991, 0.17), (1992, 0.11), (1992, 0.13), (1992, 0.15), (1992, 0.17), (1993, 0.11), (1993, 0.13), (1993, 0.15), (1993, 0.17), (1994, 0.11), (1994, 0.13), (1994, 0.15), (1994, 0.17), (1995, 0.11), (1995, 0.13), (1995, 0.15), (1995, 0.17), (1996, 0.11), (1996, 0.13), (1996, 0.15), (1996, 0.17), (1997, 0.11), (1997, 0.13), (1997, 0.15), (1997, 0.17), (1998, 0.11), (1998, 0.13), (1998, 0.15), (1998, 0.17), (1999, 0.11), (1999, 0.13), (1999, 0.15), (1999, 0.17), (2000, 0.11), (2000, 0.13), (2000, 0.15), (2000, 0.17), (2001, 0.11), (2001, 0.13), (2001, 0.15), (2001, 0.17), (2002, 0.11), (2002, 0.13), (2002, 0.15), (2002, 0.17), (2003, 0.11), (2003, 0.13), (2003, 0.15), (2003, 0.17), (2004, 0.11), (2004, 0.13), (2004, 0.15), (2004, 0.17), (2005, 0.11), (2005, 0.13), (2005, 0.15), (2005, 0.17), (2006, 0.11), (2006, 0.13), (2006, 0.15), (2006, 0.17), (2007, 0.11), (2007, 0.13), (2007, 0.

### End of Calculations                  

In [228]:
for _ in range(3):
    os.system("echo -ne '\007'")


In [229]:
df_all.query('pom==.14')

Empty DataFrame
Columns: [year, pom, no_hedge_current, no_hedge_highest, with_hedge_current, rebalanced_current]
Index: []

In [230]:
df_all

year   pom  no_hedge_current  no_hedge_highest  with_hedge_current  \
0    1990  0.11             0.073             0.078               0.073   
1    1990  0.13             0.073             0.078               0.070   
2    1990  0.15             0.073             0.078               0.070   
3    1990  0.17             0.073             0.078               0.070   
4    1991  0.11             0.078             0.083               0.078   
..    ...   ...               ...               ...                 ...   
115  2018  0.17             0.038             0.100               0.026   
116  2019  0.11             0.123             0.242               0.099   
117  2019  0.13             0.123             0.242               0.061   
118  2019  0.15             0.123             0.242               0.061   
119  2019  0.17             0.123             0.242               0.060   

     rebalanced_current  
0                 0.054  
1                 0.054  
2                 0.054  
3                 0.054  
4                 0.057  
..                  ...  
115               0.027  
116               0.091  
117               0.091  
118               0.091  
119               0.091  

[120 rows x 6 columns]

### Show example of 3d graphing

In [231]:

# df_all3 = df_all2.query("ret_type in ['with_hedge_current','rebalanced_current']")
fig = px.scatter_3d(df_all3, x='pom', y='year', z='ret',color='ret_type')
# fig.update_layout(modebar_orientation='v')
s = {'aspectmode': 'cube'}
config = dict({'scrollZoom': False})
fig.update_layout(
    legend=dict(x=-0.1, y=1.2),
    modebar={'orientation': 'v','bgcolor':'grey'}
)

fig.show(config=config)


### Run  Dash webapp

In [255]:
importlib.reload(dashapp)


<module 'dashapp.dashapp2' from '/Users/bperlman1/Documents/billybyte/pyliverisk/dashapp/dashapp/dashapp2.py'>

In [ ]:
if __name__=='__main__':
    panel_color = '#FFFFFA'
    
    # create dashapp
    dap = dashapp.DashApp()
    
    # row 1
    app_title = """Execute and Compare Put-Protected SP500 Strategies
vs
Various Buy and Hold Strategies"""
    r1 = make_page_title(app_title,div_id='r1',html_container=html.H3)                  

    # row 2 

    # ************ FIRST, create comparative returns data *******************
    init_beg_date = yyyymmdd_to_dt_string(dft.settle_date.values[0])
    init_end_date = yyyymmdd_to_dt_string(dft.settle_date.values[-1])
    init_pom = str(put_perc_otm)
    init_rebal_target = str(rebal_target)
    init_rebal_adjust = str(rebal_adjust)
    init_input_data = [init_beg_date,init_end_date,init_pom,init_rebal_target,init_rebal_adjust]
    dft_new,df_values,df_daily_values,df_rebalance_info = _get_df_values_from_input_data(init_input_data)
    dt_values,_ = dashapp.make_dashtable('dt_values',df_in=df_values,max_width=None)

    
    # ************ NOW, create row 2 *******************
    r2_style = {"font-size":"18px","text-align":"center"}
    dpr_beg_date =  dashapp.make_datepicker(dft,'beg_dp','settle_dt',style=r2_style)
    dpr_end_date =  dashapp.make_datepicker(dft,'end_dp','settle_dt',
                                            init_date=1,style=r2_style)
    put_otm_style = r2_style.copy()
    put_otm_style["position"]= "relative"
    put_otm_style["display"] = "inline-block"
    put_otm_style["width"] = "130px"
    put_otm_style["height"] = "45px"
    put_otm_inputbox = dcc.Input(
        id='put_otm_inputbox',type="number",value=put_perc_otm,
        style=put_otm_style,debounce=True,step=.001
    )
    rebal_target_inputbox = dcc.Input(
        id='rebal_target_inputbox',type="number",value=rebal_target,
        style=put_otm_style,debounce=True,step=.001
    )
    rebal_adjust_inputbox = dcc.Input(
        id='rebal_adjust_inputbox',type="number",value=rebal_adjust,
        style=put_otm_style,debounce=True,step=.001
    )
    
    #   col 1 row 1
    r2c1r1 = dashapp.multi_column_panel([html.Div("begin date: "),
                            dpr_beg_date],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 1 row 2
    r2c1r2 = dashapp.multi_column_panel([html.Div("end date: "),
                            dpr_end_date],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 1 row 3
    r2c1r3 = dashapp.multi_column_panel([html.Div("put% otm: "),
                            put_otm_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 1 row 4
    r2c1r4 = dashapp.multi_column_panel([html.Div("rebal trg%: "),
                            rebal_target_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 1 row 4
    r2c1r5 = dashapp.multi_column_panel([html.Div("rebal adj%: "),
                            rebal_adjust_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    
    # row 2 column 1
    r2c1 = dashapp.multi_row_panel([r2c1r1,r2c1r2,r2c1r3,r2c1r4,r2c1r5],panel_background_color='#A6B2E2',
                                parent_class=dashapp.pn,
                                    div_id='r2c1')
    
    #   col 2 row 1
    r2c2r1 = dashapp.nopanel_cell([html.H3("Compare Strategy Results")])
    #   col 2 row 2
    r2c2r2 = dashapp.multi_column_panel([dt_values],
                                       parent_class=dashapp.pnncnm)
    # row 2 column 2
    r2c2 = dashapp.multi_row_panel([r2c2r1,r2c2r2],                                
                                grid_template='1fr 4fr',div_id='r2c2')
    # row 2
    r2 = dashapp.multi_column_panel([r2c1,r2c2],
                                    grid_template='1fr 4fr',
                                    parent_class=dashapp.pn,
                                    div_id='r2')

    #  create a DashLink between r2c1 and the df_values DataFrame in r2c2    
    def _update_dt_values(input_data):
        dft_new,df_values,_,_ = _get_df_values_from_input_data(input_data)
        return [df_values.to_dict('rows')]
        
    r2c1_intuplist = [
        (dpr_beg_date,'date'),
        (dpr_end_date,'date'),
        (put_otm_inputbox,'value'),
        (rebal_target_inputbox,'value'),
        (rebal_adjust_inputbox,'value'),
    ]
    r2c1_outlist = [('dt_values','data')]
    r2_link = dashapp.DashLink(r2c1_intuplist,r2c1_outlist,io_callback=_update_dt_values)
    
    
    
    
#     # ************ create graph_stock_vs_cash *******************
#     init_port_values_fig = _get_graph_stock_vs_cash_figure(init_input_data)
#     graph_stock_vs_cash = dcc.Graph(id='graph_stock_vs_cash',figure=init_port_values_fig)
    
#     def _update_graph_stock_vs_cash(input_data):
#         return [_get_graph_stock_vs_cash_figure(input_data)]
#     r3_old_link = dashapp.DashLink(r2c1_intuplist,[(graph_stock_vs_cash,'figure')],
#         io_callback=_update_graph_stock_vs_cash
#     )
    
    
#     # ************ create graph_close_vs_hedge_strike *******************
#     fig_graph_close_vs_hedge_strike = _get_close_vs_hedge_figure(init_input_data)
#     graph_close_vs_hedge_strike = dcc.Graph(
#         id='graph_close_vs_hedge_strike',
#         figure=fig_graph_close_vs_hedge_strike)
    
#     def _update_graph_close_vs_hedge_strike(input_data):
#         return [_get_close_vs_hedge_figure(input_data)]
#     r4_link = dashapp.DashLink(
#         r2c1_intuplist,
#         [(graph_close_vs_hedge_strike,'figure')],
#         io_callback=_update_graph_close_vs_hedge_strike
#     )
    
#     # combine graphs into r3
#     r3_old = dashapp.multi_column_panel([graph_stock_vs_cash,graph_close_vs_hedge_strike],
#                           parent_class=dashapp.pn,
#                           div_id='r3_old')
    

    # row 3 subplot graphs
    get_close_vs_hedge_stock_vs_cash = dcc.Graph(
        id='get_close_vs_hedge_stock_vs_cash',style={'width':'90vw'})
    def _update_close_vs_hedge_stock_vs_cash(input_data):
        return [_get_close_vs_hedge_stock_vs_cash_figure(input_data)]
    r3_link = dashapp.DashLink(
        r2c1_intuplist,
        [(get_close_vs_hedge_stock_vs_cash,'figure')],
        io_callback=_update_close_vs_hedge_stock_vs_cash
    )
    
    r3 = dashapp.multi_column_panel([get_close_vs_hedge_stock_vs_cash],
                          parent_class=dashapp.pn,
                          div_id='r3')
    
    
    
    # ************ create row 4 *******************
    dt_dft,link_for_dynamic_paging = dashapp.make_dashtable(
        'dt_dtc',df_in=dft,filtering=True,displayed_rows=0)
    r4 = dashapp.panel_cell([dt_dft],div_id='r4')
    
    # *********** create row 5 ********************
    app_title2 = """
    Show groups of scenarios
    """
    r5 = make_page_title(app_title2,div_id='r5',html_container=html.H3)                  

    
    #   col 1 
    init_beg_year = df_all.year.min()
    beg_year_inputbox = dcc.Input(
        id='beg_year_inputbox',type="number",value=int(init_beg_year),
        style=put_otm_style,debounce=True,step=1
    )    
    r6c1 = dashapp.multi_column_panel([html.Div("begin year: "),
                            beg_year_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 2
    init_end_year = df_all.year.max()
    end_year_inputbox = dcc.Input(
        id='end_year_inputbox',type="number",value=int(init_end_year),
        style=put_otm_style,debounce=True,step=1
    )    
    r6c2 = dashapp.multi_column_panel([html.Div("end year: "),
                            end_year_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 3
    init_low_pom = df_all.pom.min()
    low_pom_inputbox = dcc.Input(
        id='low_pom_inputbox',type="number",value=init_low_pom,
        style=put_otm_style,debounce=True,step=.001
    )    
    r6c3 = dashapp.multi_column_panel([html.Div("low% otm: "),
                            low_pom_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    #   col 4
    init_high_pom = df_all.pom.max()
    high_pom_inputbox = dcc.Input(
        id='high_pom_inputbox',type="number",value=init_high_pom,
        style=put_otm_style,debounce=True,step=.001
    )    
    r6c4 = dashapp.multi_column_panel([html.Div("high% otm: "),
                            high_pom_inputbox],grid_template=['1fr 3fr'],
                                        parent_class="aligncenter")
    r6 = dashapp.multi_column_panel([r6c1,r6c2,r6c3,r6c4],
                          parent_class=dashapp.pn,
                          div_id='r6')
    
    data_store = dcc.Store(id='data_store')
    data_store_loading = dcc.Loading(
        id='data_store_loading',children=[data_store],fullscreen=True)
    data_store_link = dashapp.DashLink(
        scenario_inputs,[(data_store,'data')],
        io_callback=_get_scenarios_data
    )
    
    scenario_inputboxes = [beg_year_inputbox,end_year_inputbox,low_pom_inputbox,high_pom_inputbox]
    scenario_inputs = [(v,'value') for v in scenario_inputboxes]
    no_zoom_config = dict({'scrollZoom': False})
    #
    graph_multi_scenarios = dcc.Graph(
        id='graph_multi_scenarios',config=no_zoom_config,style={'width':'45vw'})
    def _update_multi_scenarios(input_data):
        f = _get_scenarios_figure_from_data(input_data)
        return [f]
    graph_multi_scenarios_link = dashapp.DashLink(
        [(data_store,'data')],
        [(graph_multi_scenarios,'figure')],
        io_callback=_update_multi_scenarios
    )
    dt_multi_scenarios_title = make_page_title(
        """
        All Data
        """,
        html_container=html.H3)                  
    dt_multi_scenarios,dt_multi_scenarios_nav_link = dashapp.make_dashtable(
        "dt_multi_scenarios",df_all,input_store=data_store,
        input_store_key='df_all',max_width=None)
    
    # row 7 col 1 
#     r7c1 = dashapp.multi_column_panel([graph_multi_scenarios])
    r7c1 = dashapp.panel_cell(graph_multi_scenarios)
    # row 7 col 2 row 1 
    r7c2r1 = dt_multi_scenarios_title
    # row 7 col 2 row 2
#     r7c2r2 = dashapp.multi_column_panel([dt_multi_scenarios],
#                                        parent_class=dashapp.pnncnm)
    r7c2r2 = html.Div(dt_multi_scenarios,style={'width':'45vw'})
    # row 7 col 2s
    r7c2 = dashapp.multi_row_panel([r7c2r1,r7c2r2],                                
                                grid_template='1fr 4fr',div_id='r7c2')
    # row 7
    r7 = dashapp.multi_column_panel([r7c1,r7c2],
                                    grid_template='1fr 1fr',
                                    parent_class=dashapp.pn,
                                    div_id='r7')   
    
#     dap.add_links([link_for_dynamic_paging,r2_link,r3_link,
#                    r4_link,graph_multi_scenarios_link,dt_multi_scenarios_nav_link,
#                    data_store_link])
    dap.add_links([link_for_dynamic_paging,r2_link,r3_link,
                   graph_multi_scenarios_link,dt_multi_scenarios_nav_link,
                   data_store_link])
    # all rows
    all_rows = html.Div([r1,r2,r3,r4,r5,r6,r7,data_store_loading])
    dap.create_app(all_rows,app_title='example2',app_port=8804)
    

2020-05-28 07:12:42,938 - root - DEBUG - dt_values entering create_dt_div
2020-05-28 07:12:42,940 - root - DEBUG - dt_values exiting create_dt_div
2020-05-28 07:12:42,944 - root - DEBUG - dt_dtc entering create_dt_div
2020-05-28 07:12:42,947 - root - DEBUG - dt_dtc exiting create_dt_div
2020-05-28 07:12:42,952 - root - DEBUG - dt_multi_scenarios entering create_dt_div
2020-05-28 07:12:42,955 - root - DEBUG - dt_multi_scenarios exiting create_dt_div


_get_df_values_from_input_data input_data: ['1990-05-25', '2020-05-21', '0.14', '0.6', '0.7']


2020-05-28 07:12:42,981 - root - INFO - This app will run at the URL: http://127.0.0.1:8804


 * Serving Flask app "dashapp.dashapp2" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


2020-05-28 07:12:42,991 - werkzeug - INFO -  * Running on http://127.0.0.1:8804/ (Press CTRL+C to quit)
2020-05-28 07:12:47,170 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET / HTTP/1.1" 200 -
2020-05-28 07:12:47,238 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET /assets/custom.css?m=1583299996.0 HTTP/1.1" 304 -
2020-05-28 07:12:47,241 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET /assets/dashapp_example_3_rows.css?m=1585932241.0 HTTP/1.1" 304 -
2020-05-28 07:12:47,243 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET /assets/styles.css?m=1589206170.0 HTTP/1.1" 304 -
2020-05-28 07:12:47,338 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET /_dash-layout HTTP/1.1" 200 -
2020-05-28 07:12:47,340 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET /_dash-dependencies HTTP/1.1" 200 -
2020-05-28 07:12:47,353 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "GET /_favicon.ico?v=1.11.0 HTTP/1.1" 200 -


...

2020-05-28 07:12:47,579 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:47] "POST /_dash-update-component HTTP/1.1" 200 -


_dash_table_update_paging_closure: page_current:0 page_size: 0


2020-05-28 07:12:48,937 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:48] "POST /_dash-update-component HTTP/1.1" 200 -
2020-05-28 07:12:49,175 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:12:49] "POST /_dash-update-component HTTP/1.1" 200 -
2020-05-28 07:13:02,479 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:13:02] "POST /_dash-update-component HTTP/1.1" 200 -
2020-05-28 07:13:02,546 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:13:02] "POST /_dash-update-component HTTP/1.1" 200 -



_dash_table_update_paging_closure: page_current:0 page_size: 20


2020-05-28 07:13:02,811 - werkzeug - INFO - 127.0.0.1 - - [28/May/2020 07:13:02] "POST /_dash-update-component HTTP/1.1" 200 -


### Create a dataframe that holds a "base" volskew, representing a volskew with:
1. the median S&P vol skew 10% below the money, for options on the CME ES contract from 2011 to 2020
2. the vol skew of the rows from number 1, that has the median skew 10% above the money

In [23]:
df_iv_skew_ES = pd.read_csv('iv_skew_ES_2011_2020.csv')

df_iv_skew_ES2 = df_iv_skew_ES[df_iv_skew_ES['-0.1'] == df_iv_skew_ES['-0.1'].median()]
df_iv_skew_ES2 = df_iv_skew_ES2[df_iv_skew_ES2['0.1'] == df_iv_skew_ES2['0.1'].median()]
df_only_strikes = df_iv_skew_ES2.iloc[0:1][[c for c in df_iv_skew_ES2.columns.values if '.' in c]]
strikes = [round(float(c),2) for c in  df_only_strikes.columns.values]
skews = df_only_strikes.iloc[0].values
df_skew = pd.DataFrame({'strike':strikes,'vol_skew':skews})
df_skew.index = df_skew.strike
df_skew = df_skew[['vol_skew']]
def _calc_skew_from_df_skew(underlying_price,strike):
    curr_perc_otm = round(strike/underlying_price - 1,5)
    df_skew2 = df_skew.copy()
    row_to_append = df_skew2.iloc[-1]
    row_to_append.name = curr_perc_otm
    row_to_append['vol_skew'] = np.nan
    df_skew2 = df_skew2.append(row_to_append)
    df_skew2 = df_skew2.sort_index()
    df_skew2['vol_skew'] = df_skew2.vol_skew.interpolate(method='polynomial', order=2)
    skew = df_skew2.loc[curr_perc_otm,'vol_skew']
    return skew




In [24]:
# test it - value should be about 0.0653434
_calc_skew_from_df_skew(2900,2900*(1-.12345))


0.065343393830266

In [25]:
def _same_strike_hedge(r):  
    skew_for_hedge = _calc_skew_from_df_skew(r.close,r.current_hedge_strike)
    hedge = black.black('p', r.close, r.current_hedge_strike, years_to_hedge, .02, skew_for_hedge)
    return hedge
    
dft_hedge_noroll = dft[(dft.days_of_hedge==years_to_hedge*365) & (dft.time_to_hedge==False)]
dft_hedge_noroll.apply(_same_strike_hedge,axis=1).sum(),dft.hedge.sum()

(4.807831568677079, 957.6066548030537)

## END